# 12. 社群網路分析



## 安裝套件 & 連接雲端資料夾 & 讀取資料

In [ ]:
!pip install pandas
!pip install numpy
!pip install pyvis
!pip install networkx
!pip install IPython

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 756.0/756.0 kB 44.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 67.0 MB/s eta 0:00:00


In [ ]:
import pandas as pd
import numpy as np
import pyvis
import networkx as nx
import IPython

連結雲端資料夾

In [ ]:
import os

from google.colab import drive
drive.mount('/content/drive')

os.chdir('/content/drive/MyDrive/Colab Notebooks') #切換該目錄
os.listdir() #確認目錄內容

Mounted at /content/drive


['Arial Unicode MS.ttf',
 'SourceHanSansTW-Regular.otf',
 'colab',
 'classification_with_embeddings.ipynb',
 'TaipeiSansTCBeta-Regular.ttf',
 'text_embeddings.ipynb',
 '印巴.csv',
 '俄烏-20240101-20250518.csv',
 'dict',
 'LDA',
 'BERT',
 'pig_team_bert.ipynb',
 'data',
 'LLM_Inference_application.ipynb',
 'Z_05-pig_team-llm.ipynb',
 '俄烏.csv',
 '01-pig_team.ipynb',
 'lda_zh.html',
 '02-pig_team_lda.ipynb',
 'data.zip',
 'week12_bert.ipynb',
 'pos_table_俄烏.csv',
 'sentence_table_俄烏.csv',
 'entity_table_俄烏.csv',
 '03-pig_team_bert.ipynb',
 '04-pig_term_ner.ipynb',
 '05_pig_team_LLM.ipynb',
 'pers_netWork.html',
 'basic_netWork.html',
 'max_sub.html',
 '06-pig_Social_Media.ipynb']

讀取資料


In [ ]:
raw_data = pd.read_csv('./俄烏.csv')
raw_data = raw_data[raw_data.artComment != '[]']
raw_data = raw_data.sample(round(raw_data.shape[0]/4), random_state=2024)
print(raw_data.shape)
raw_data.head()

(3172, 11)


system_id                                             artUrl  \
2765        2766  https://www.ptt.cc/bbs/Gossiping/M.1656838316....   
9             10  https://www.ptt.cc/bbs/Gossiping/M.1645681125....   
8866        3226  https://www.ptt.cc/bbs/Gossiping/M.1713144379....   
12595       6955  https://www.ptt.cc/bbs/HatePolitics/M.17402036...   
4954        4955  https://www.ptt.cc/bbs/HatePolitics/M.16513410...   

                          artTitle              artDate     artPoster  \
2765   Re:[新聞]PTT有人對烏俄戰爭抱持投降主義綠委要求  2022-07-03 16:51:54          Win7   
9              [問卦]烏俄戰爭一觸即發台灣看了不怕嗎  2022-02-24 13:38:43  wang19980531   
8866                 [問卦]烏克蘭已經輸了？！  2024-04-15 09:26:17         kll95   
12595            Re:[討論]受到侵略應該抵抗嗎？  2025-02-22 13:54:47       cc1plus   
4954             [討論]黃世聰是什麼都懂的斜槓男神  2022-05-01 01:50:10        oftisa   

        artCatagory                                         artContent  \
2765      Gossiping  請問蔡委員祖上\n\n施琅來台有沒有跪？\n日本人來台有沒有跪？\n國民黨來台有沒有跪？\n...   
9         Gossiping  烏克蘭和俄羅斯的戰爭一觸即發\n股票、數位貨幣大跳水\n反觀中國大陸與台灣的關係\n也處於緊...   
8866      Gossiping  烏俄戰爭已經走到尾聲\n\n澤倫斯基目前應該是暗中準備逃亡\n\n美援基本被一些官員貪污給敗...   
12595  HatePolitics  站在國家觀點當然是要抵抗, 站在人民觀點這就不一定\n但是也沒辦法有個統一的講法, 值不值得...   
4954   HatePolitics  黃世聰的頭銜是財經專家，但是烏俄戰爭也會講，還是可以上主持台講主Key，連戰術戰略\n都懂，...   

                                              artComment             e_ip  \
2765   [{"cmtStatus": "→", "cmtPoster": "coollfd", "c...       1.200.97.6   
9      [{"cmtStatus": "推", "cmtPoster": "currry", "cm...   101.12.100.162   
8866   [{"cmtStatus": "推", "cmtPoster": "xzcb2008", "...   111.80.215.113   
12595  [{"cmtStatus": "噓", "cmtPoster": "xa9277178", ...     1.162.77.111   
4954   [{"cmtStatus": "推", "cmtPoster": "holyhelm", "...  220.141.113.181   

              insertedDate dataSource  
2765   2022-07-04 01:29:34        ptt  
9      2022-02-25 00:33:57        ptt  
8866   2024-04-16 01:30:52        ptt  
12595  2025-02-23 01:29:56        ptt  
4954   2022-05-01 01:46:58        ptt

## 11.1 查看發文者與留言者關係

取得留言者跟狀態（推）

In [ ]:
raw_data = raw_data.iloc[20:240].reset_index(drop=True)
#因為爬下來的raw_data jason檔格式有錯誤，故再從其中篩選出幾筆沒問題的資料進行分析

In [ ]:
# parse comment
# 處理某篇文章的所有留言（取出留言者與狀態）
def getComtInfo(com):
  cmters,cmt_statuss = [],[]
  com = eval(com)
  for i in com:
    # print(i)
    cmters.append(i['cmtPoster'])
    cmt_statuss.append(i['cmtStatus'])
  return pd.Series([cmters, cmt_statuss])

raw_data[['artComter','artStatus']] = raw_data['artComment'].apply(lambda r: getComtInfo(r))
raw_data.head()

system_id                                             artUrl  \
0        237  https://www.ptt.cc/bbs/Gossiping/M.1675610483....   
1       2994  https://www.ptt.cc/bbs/Gossiping/M.1658987368....   
2       1316  https://www.ptt.cc/bbs/Gossiping/M.1685763404....   
3       1116  https://www.ptt.cc/bbs/Gossiping/M.1683254760....   
4       2565  https://www.ptt.cc/bbs/Gossiping/M.1655559188....   

                    artTitle              artDate   artPoster artCatagory  \
0     [新聞]沈伯洋揭中共認知戰手段捐錢操縱網紅影  2023-02-05 23:21:21    jason486   Gossiping   
1      [問卦]今晚政論節目會怎麼討論論文門事件?  2022-07-28 13:49:24    jeff0025   Gossiping   
2  Re:[問卦]我就問一句家庭真的不是講理的地方嗎?  2023-06-03 11:36:40     ffreakk   Gossiping   
3                [爆卦]工廠另類漲電費  2023-05-05 10:45:53     roudolf   Gossiping   
4             [問卦]烏俄士兵會整理內務嗎  2022-06-18 21:33:05  a000209898   Gossiping   

                                          artContent  \
0  沈伯洋揭中共認知戰手段 捐錢操縱網紅影響輿論\n\n2023/2/5 20:25（2/5 2...   
1  今天早上堅哥律師出來開記者會表明從目前證據看起來根本不是抄襲\n\n結果下午馬上另一邊的律師...   
2  家庭是權力遊戲的地方\n\n權力結構是看錢誰賺的多\n\n但是也不一定賺錢多的地位高\n\n...   
3  https://hvcs.taipower.com.tw/\n112年起 夏季電價由\n\n...   
4  烏俄戰爭現在在烏克蘭東部，戰鬥十分激烈，每天都有數百人陣亡\n那些士兵在睡覺的時候，棉被會折...   

                                          artComment            e_ip  \
0  [{"cmtStatus": "噓", "cmtPoster": "nfhlve", "cm...  118.166.66.212   
1  [{"cmtStatus": "推", "cmtPoster": "greensaru", ...  175.98.141.254   
2  [{"cmtStatus": "→", "cmtPoster": "zanns", "cmt...   101.12.20.158   
3  [{"cmtStatus": "推", "cmtPoster": "SaintSeven",...   111.71.215.85   
4  [{"cmtStatus": "→", "cmtPoster": "k385476916",...  218.164.82.206   

          insertedDate dataSource  \
0  2023-02-06 01:24:54        ptt   
1  2022-07-29 01:33:57        ptt   
2  2023-06-04 01:35:32        ptt   
3  2023-05-06 01:31:23        ptt   
4  2022-06-19 01:40:29        ptt   

                                           artComter  \
0  [nfhlve, cooleagles, amfive, Takano34, kinki99...   
1  [greensaru, monitor, goldcity5, Rigogo, pttxo,...   
2        [zanns, whitenoise, avigale, avigale, inse]   
3  [SaintSeven, virgil7518, mugigi, jokc7839, jil...   
4  [k385476916, shine32025, joumay, pinhanpaul, a...   

                                           artStatus  
0  [噓, 噓, 噓, →, 噓, 推, →, 推, 噓, 推, 噓, 推, 噓, 噓, →, ...  
1  [推, →, →, 推, →, →, →, 推, 推, 推, →, 噓, 推, 推, →, ...  
2                                    [→, 推, →, →, →]  
3  [推, →, 推, 推, →, →, →, 推, →, →, 噓, →, 推, 推, 推, ...  
4               [→, →, →, 推, 推, →, →, 推, →, 推, →, 推]

依據每一筆留言展開

In [ ]:
raw_data = raw_data.explode(['artComter','artStatus'])
socail_data = raw_data[['artUrl','artPoster','artComter','artStatus']]
socail_data.head(10)

artUrl artPoster     artComter  \
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486        nfhlve   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486    cooleagles   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486        amfive   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486      Takano34   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486      kinki999   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486     maxinehou   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486      Gallardo   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486    wilson3435   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486      tomshiou   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486  AustinRivers   

  artStatus  
0         噓  
0         噓  
0         噓  
0         →  
0         噓  
0         推  
0         →  
0         推  
0         噓  
0         推

查看留言狀態

In [ ]:
socail_data.artStatus.unique()

array(['噓', '→', '推'], dtype=object)

建立邊的資料

In [ ]:
import random

# 發文者對文章
po_df = socail_data[['artPoster','artUrl']].drop_duplicates().rename(columns = {'artPoster':'src','artUrl':'dis'})

# sample 300 篇文章
random.seed(2024)
sample_url = random.choices(po_df.dis.unique().tolist(),k=300)
po_df = po_df[po_df.dis.isin(sample_url)]

# 留言者對文章，狀態為 weight
re_df = socail_data[['artComter','artUrl','artStatus']].rename(columns = {'artComter':'src','artUrl':'dis','artStatus':'weight'})
re_df = re_df[re_df.dis.isin(sample_url)]
re_df = re_df[~re_df['src'].isna()]
re_df.head()

src                                                dis weight
0      nfhlve  https://www.ptt.cc/bbs/Gossiping/M.1675610483....      噓
0  cooleagles  https://www.ptt.cc/bbs/Gossiping/M.1675610483....      噓
0      amfive  https://www.ptt.cc/bbs/Gossiping/M.1675610483....      噓
0    Takano34  https://www.ptt.cc/bbs/Gossiping/M.1675610483....      →
0    kinki999  https://www.ptt.cc/bbs/Gossiping/M.1675610483....      噓

計算某留言者對文章的總評論分數
- 轉換邊的狀態 -> weight

In [ ]:
def convertStatus(s):
  if s == '推':
    return 2
  elif s == '→':
    return 1
  else :
    return -1
re_df['weight'] = re_df['weight'].map(convertStatus)
# 計算某位留言者對某篇文章的總分數
re_df = re_df.groupby(['src','dis']).sum().reset_index()
re_df

src                                                dis  weight
0      A0091127  https://www.ptt.cc/bbs/Gossiping/M.1652752043....       2
1      A80211ab  https://www.ptt.cc/bbs/Gossiping/M.1645871388....       2
2      A80211ab  https://www.ptt.cc/bbs/Gossiping/M.1672119879....      -1
3      A80211ab  https://www.ptt.cc/bbs/Gossiping/M.1678145965....      -1
4     ABiao0220  https://www.ptt.cc/bbs/Gossiping/M.1689388176....       4
...         ...                                                ...     ...
5090       zyra  https://www.ptt.cc/bbs/Gossiping/M.1653112723....       2
5091       zzro  https://www.ptt.cc/bbs/Gossiping/M.1649237794....       2
5092       zzro  https://www.ptt.cc/bbs/Gossiping/M.1665583811....       2
5093   zzyyxx77  https://www.ptt.cc/bbs/Gossiping/M.1645696480....       2
5094   zzzzaaaa  https://www.ptt.cc/bbs/Gossiping/M.1664510836....       2

[5095 rows x 3 columns]

In [ ]:
# 設定分數低的為紅色
def getColor(w):
  if w>0:
    return 'green'
  else:
    return 'red'
re_df['color'] = re_df.weight.map(getColor)
re_df

src                                                dis  weight  \
0      A0091127  https://www.ptt.cc/bbs/Gossiping/M.1652752043....       2   
1      A80211ab  https://www.ptt.cc/bbs/Gossiping/M.1645871388....       2   
2      A80211ab  https://www.ptt.cc/bbs/Gossiping/M.1672119879....      -1   
3      A80211ab  https://www.ptt.cc/bbs/Gossiping/M.1678145965....      -1   
4     ABiao0220  https://www.ptt.cc/bbs/Gossiping/M.1689388176....       4   
...         ...                                                ...     ...   
5090       zyra  https://www.ptt.cc/bbs/Gossiping/M.1653112723....       2   
5091       zzro  https://www.ptt.cc/bbs/Gossiping/M.1649237794....       2   
5092       zzro  https://www.ptt.cc/bbs/Gossiping/M.1665583811....       2   
5093   zzyyxx77  https://www.ptt.cc/bbs/Gossiping/M.1645696480....       2   
5094   zzzzaaaa  https://www.ptt.cc/bbs/Gossiping/M.1664510836....       2   

      color  
0     green  
1     green  
2       red  
3       red  
4     green  
...     ...  
5090  green  
5091  green  
5092  green  
5093  green  
5094  green  

[5095 rows x 4 columns]

製作網路圖

In [ ]:
# 人為綠色節點
# po文為橘色節點

# 建立一個網路圖
netWork = pyvis.network.Network(notebook=True, cdn_resources='in_line',directed=True)
# 所有發文者＋留言者
person = list(set(po_df.src.unique().tolist()+re_df.src.unique().tolist()))
url = po_df.dis.unique().tolist()

# 加入節點（人）
netWork.add_nodes(
    nodes = person,
    value = [1 for i in range(len(person))],
    color = ['#66CDAA' for i in range(len(person))],
    title = person
)
# 加入節點（文章）
netWork.add_nodes(
    nodes = url,
    value = [2 for i in range(len(url))],
    color = ['#FFB366' for i in range(len(url))],
    title = url
)

# 加入邊（發文者 -> 文章）
for i in po_df.to_numpy():
  netWork.add_edge(i[0],i[1],width = 2,color='grey')
# 加入邊（留言者 -> 文章），顏色為某發文者對該文章的總分（>0:綠; <=0:紅）
for i in re_df.to_numpy():
  netWork.add_edge(i[0],i[1],width = 2,color=i[3])

# 設定layout，圖節點之間的斥力
netWork.repulsion()

# netWork.show("./basic_netWork.html")
netWork.save_graph("./basic_netWork.html")
IPython.display.HTML('basic_netWork.html')

**說明：**  
橘色節點代表發文者，下面的連結是文章的連結，旁邊節點（留言者）指向發文者。  
綠色邊（箭頭）代表留言者的留言總分大於0，留言為**正向或中立**。    
紅色邊（箭頭）代表留言者的留言總分小於0，留言為**負向**。

透過此網路圖可以發現：
- 大部分的文章都是中立或正向的留言。
- 有幾篇留言較多的文章，紅色以及綠色的邊分布看起來各半，推測是因為這篇文章的內容討論空間較大（或較具有爭議性），能夠引起正、反兩方的討論，且兩方的交流相當激烈。
- 另外，也可以從此圖中發現有留言者會到不同的文章留言負向的言論，若在圖中發現這樣的留言者所畫出的紅色邊很多，也可以把他判別為所謂的「鬧版」人物。（代表他的言論可能有待商榷）

## 11.2 查看網友之間的關係

In [ ]:
pos_cmt = socail_data.copy()
pos_cmt = pos_cmt[~pos_cmt.artComter.isna()]
pos_cmt.head(10)

artUrl artPoster     artComter  \
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486        nfhlve   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486    cooleagles   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486        amfive   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486      Takano34   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486      kinki999   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486     maxinehou   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486      Gallardo   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486    wilson3435   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486      tomshiou   
0  https://www.ptt.cc/bbs/Gossiping/M.1675610483....  jason486  AustinRivers   

  artStatus  
0         噓  
0         噓  
0         噓  
0         →  
0         噓  
0         推  
0         →  
0         推  
0         噓  
0         推

In [ ]:
pos_cmt['score'] = pos_cmt['artStatus'].apply(lambda r: convertStatus(r))

# 某留言者對某發文者的總分
pos_cmt = pos_cmt.groupby(['artComter','artPoster']).sum('score').reset_index()
pos_cmt = pos_cmt[pos_cmt.score>=0]
pos_cmt = pos_cmt[pos_cmt.artComter != pos_cmt.artPoster]
# pos_cmt.score = 1
pos_cmt

artComter     artPoster  score
0         A0091127        fomo77      2
1              A15       BBQ2591      2
2         A80211ab    Future0529      2
5        ABiao0220    NTKingsman      4
7          ADexter          F16V      2
...            ...           ...    ...
7196          zzro   Wojnarowski      2
7197      zzyyxx77      zxc36mn7      2
7198      zzzzaaaa  LoveMakeLove      3
7199      zzzzaaaa    gsp0309099      2
7200  zzzzzzzzzzzy    Supergreen      2

[6049 rows x 3 columns]

In [ ]:
mat = pd.pivot_table(pos_cmt,index = 'artComter', columns = 'artPoster' ,values='score').fillna(0)
mat

artPoster     AMDMARSHAL  Aliensoul  Allen0315  Anderson0819  AntiEntropy  \
artComter                                                                   
A0091127             0.0        0.0        0.0           0.0          0.0   
A15                  0.0        0.0        0.0           0.0          0.0   
A80211ab             0.0        0.0        0.0           0.0          0.0   
ABiao0220            0.0        0.0        0.0           0.0          0.0   
ADexter              0.0        0.0        0.0           0.0          0.0   
...                  ...        ...        ...           ...          ...   
zzh1014              0.0        0.0        0.0           0.0          0.0   
zzro                 0.0        0.0        0.0           0.0          0.0   
zzyyxx77             0.0        0.0        0.0           0.0          0.0   
zzzzaaaa             0.0        0.0        0.0           0.0          0.0   
zzzzzzzzzzzy         0.0        0.0        0.0           0.0          0.0   

artPoster     Aswind  BBQ2591  CREA  CenaC  CuLiZn5566  ...  w510048  \
artComter                                               ...            
A0091127         0.0      0.0   0.0    0.0         0.0  ...      0.0   
A15              0.0      2.0   0.0    0.0         0.0  ...      0.0   
A80211ab         0.0      0.0   0.0    0.0         0.0  ...      0.0   
ABiao0220        0.0      0.0   0.0    0.0         0.0  ...      0.0   
ADexter          0.0      0.0   0.0    0.0         0.0  ...      0.0   
...              ...      ...   ...    ...         ...  ...      ...   
zzh1014          0.0      0.0   0.0    0.0         0.0  ...      0.0   
zzro             0.0      0.0   2.0    0.0         0.0  ...      0.0   
zzyyxx77         0.0      0.0   0.0    0.0         0.0  ...      0.0   
zzzzaaaa         0.0      0.0   0.0    0.0         0.0  ...      0.0   
zzzzzzzzzzzy     0.0      0.0   0.0    0.0         0.0  ...      0.0   

artPoster     wahaha99  where823  wsad50232  wusbetz  wwl0909  xyz4594  \
artComter                                                                
A0091127           0.0       0.0        0.0      0.0      0.0      0.0   
A15                0.0       0.0        0.0      0.0      0.0      0.0   
A80211ab           0.0       0.0        0.0      0.0      0.0      0.0   
ABiao0220          0.0       0.0        0.0      0.0      0.0      0.0   
ADexter            0.0       0.0        0.0      0.0      0.0      0.0   
...                ...       ...        ...      ...      ...      ...   
zzh1014            0.0       0.0        0.0      0.0      0.0      0.0   
zzro               0.0       0.0        0.0      0.0      0.0      0.0   
zzyyxx77           0.0       0.0        0.0      0.0      0.0      0.0   
zzzzaaaa           0.0       0.0        0.0      0.0      0.0      0.0   
zzzzzzzzzzzy       0.0       0.0        0.0      0.0      0.0      0.0   

artPoster     yangzy  zkowntu  zxc36mn7  
artComter                                
A0091127         0.0      0.0       0.0  
A15              0.0      0.0       0.0  
A80211ab         0.0      0.0       0.0  
ABiao0220        0.0      0.0       0.0  
ADexter          0.0      0.0       0.0  
...              ...      ...       ...  
zzh1014          0.0      0.0       0.0  
zzro             0.0      0.0       0.0  
zzyyxx77         0.0      0.0       2.0  
zzzzaaaa         0.0      0.0       0.0  
zzzzzzzzzzzy     0.0      0.0       0.0  

[4249 rows x 185 columns]

計算網友之間的分數矩陣
- mat: 有方向性，A -> B 分數與 B -> A 分數不一定一樣。
- mat_s: 無方向性（互動總分），A -> B 分數 +  B -> A 分數

In [ ]:
# 所有留言者與發文者
pers = np.unique(pos_cmt[['artComter', 'artPoster']])

# 建立評分矩陣（留言者對發文者分數）
# 取得所有人對於其他人的分數（有方向性）
# 矩陣中的值 mat[i][j] 代表使用者 pers[i]（留言者）對使用者 pers[j]（發文者）的評分，
    # 留言者和發文者之間的關係是有方向的（即，mat[i][j] 不一定等於 mat[j][i]）
mat = pd.pivot_table(pos_cmt,index = 'artComter', columns = 'artPoster' ,values='score' ).fillna(0)\
  .reindex(columns=pers, index=pers, fill_value=0).to_numpy()
print(mat.shape)

# 取得所有人與其他人互動分數總和（無方向，兩個方向分數相加）
# 矩陣中的每一對元素都對稱，即 mat_s[i][j] 等於 mat_s[j][i]
# 對稱矩陣中的值 mat_s[i][j] 表示使用者 pers[i] 與使用者 pers[j] 之間的互動總分。
    # 透過將 pers[i] 對 pers[j] 的評分和 pers[j] 對 pers[i] 的評分相加而得到的。
# np.tril(mat, -1): 生成一個下三角矩陣（包括主對角線下方的所有元素，但不包括主對角線上的元素）
# np.triu(mat, 1): 生成一個上三角矩陣（包括主對角線上方的所有元素，但不包括主對角線上的元素）
tri = (np.tril(mat,-1).T + np.triu(mat,1))
mat_s = tri+tri.T # 上三角和下三角都包括在內，但對角線是 0
mat_s


(4394, 4394)


array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

matPresentGraph()：用來將矩陣轉換為視覺化的網絡圖
- 利用 pyvis 來繪製網絡圖，並設定節點和邊的顏色。

In [ ]:
# 產生隨機的顏色，畫圖使用
def random_color():
  r = lambda: random.randint(0,255)
  return '#%02X%02X%02X' % (r(),r(),r())

def matPresentGraph(mat:np.array, node_id:list, node_type:list=None, node_value:list=None, directed=True, edge_color=None) -> pyvis.network.Network:
  # 有方向或無方向
  if directed != True:
    # 矩陣對稱
    if (mat == mat.transpose()).all():
      print('matrix is Symmetric')
    # 矩陣不對稱
    else:
      print('matrix is not Symmetric')

  # 設定節點的類別及顏色
  # 沒有分節點類別
  if node_type == None:
    c = random_color()
    node_colors = [c for i in range(len(node_id))]
    node_type = [" " for i in range(len(node_id))]
  # 有分節點類別
  else:
    node_color_map = {}
    for i in set(node_type):
      # 幫每個類別產生一個顏色
      while True:
        c = random_color()
        if c not in node_color_map.values():
          break
      node_color_map[i] = c
    node_colors = [node_color_map[i] for i in node_type]
  # print(node_colors)

  # 如果沒有給邊的顏色，隨機產生一個
  if edge_color == None:
    edge_color = random_color()

  # 如果沒有給 node 值，就都分配 1
  if node_value == None:
    node_value = [1 for i in range(len(node_id))]

  # 建立圖
  net = pyvis.network.Network(notebook=True, directed = directed, cdn_resources='in_line')

  titles_list = []
  for i ,j in zip(node_id,node_type):
    titles_list.append(str(i)+":"+str(j))

  net.add_nodes(
      nodes = node_id,
      value = node_value,
      label = node_id,
      title = titles_list,
      color = node_colors
  )

  for row in range(len(node_id)):
    for col in range(len(node_id)):
      if mat[row][col]>0.:
        net.add_edge(
            node_id[row],node_id[col],width = mat[row][col],color = edge_color,title = mat[row][col]
        )
  net.repulsion()
  return net


設定網友的節點類型（同時為發文、留言者 / 發文者 / 留言者）

In [ ]:
# 定義發文者（po）、評論者(cmt)、兩者兼具(both)
node_type = []

cmt_list = pos_cmt['artComter'].unique().tolist()
po_list = pos_cmt['artPoster'].unique().tolist()
both_list = list(set(cmt_list) & set(po_list))
for p in pers:
  if p in both_list:
    node_type.append('both')

  elif p in cmt_list:
    node_type.append('cmt')

  elif p in po_list:
    node_type.append('po')


In [ ]:
net = matPresentGraph(mat=mat, node_id=pers, node_type=node_type)
net.save_graph("./pers_netWork.html")
IPython.display.HTML('pers_netWork.html')

**說明：**  
中間節點（顏色粉色）是發文者，紫色節點是留言者。  
邊的粗細代表的是留言者對該發文者的分數，越粗代表累積分數越高。

**從圖表中可以：**
- 看出網友間的關係（無論是發文者或留言者都能清楚顯示出）。
- 找出活躍於「俄烏戰爭議題」的網友，看出哪些發文者發的文章有較多的網友參與討論。


## 11.3 Measures on graph

Transitivity/Density/Distance/Diameter/Clustering

計算最大的subgraph 的 measure

In [ ]:
# 計算max subgraph
G = nx.Graph(mat_s)
G_sub = sorted(nx.connected_components(G), key=len, reverse=True)
G_max_sub = G.subgraph(G_sub[0])
# # 重新定義 mat
sub_mat = nx.adjacency_matrix(G_max_sub).todense()
node_idx = list(G_max_sub.nodes)
sub_pers = pers[node_idx]


畫出最大subgraph

In [ ]:
net = matPresentGraph(mat=sub_mat,node_id=sub_pers,directed=False)
net.save_graph("./max_sub.html")
IPython.display.HTML('max_sub.html')

matrix is Symmetric


透過最大的 subgraph 可以看出：  

- 哪些群體的連接更加緊密，代表該群體中的成員彼此之間互動頻繁。
- 找出位於中間節點（連接邊最多）的人，代表他們在群體中較能影響他人的意見。

根據此圖可以看出在PTT討論俄烏戰爭主要的群體，以及較能扮演意見領袖（或引起他人討論）的人，並且也可以找出對於此議題有較多關心的人，了解他們之間的互動為何。

計算 transitivity
- transitivity 是衡量一個圖 (graph) 中閉合三角形比例的指標。在社交網絡或其他連結圖中，它反映了節點之間形成緊密社群的程度。


In [ ]:
nx.transitivity(nx.Graph(sub_mat))

0.0006585314041588973

- 可以發現transitivity是0，表示圖中不存在任何三角形，再重複檢查一次上面的subgram，證實圖中並不存在三角形。  

- 代表著圖中的節點之間的連接較為鬆散，並且圖的結構可能不穩定，可能表示在ptt俄烏衝突議題的社交網路中，用戶之間的聯繫並不緊密。

計算 density （實際 edge 數/最大 edge 數）

- density可以用來衡量圖的緊密程度。

In [ ]:
nx.density(nx.Graph(sub_mat))

0.0006436521610684692

- 在此社群網路中，圖的密度很低，表示用戶之間的聯繫並不緊密，訊息不容易在網路中傳播。

計算 distance（平均每兩個節點的 shortest path 長度）

In [ ]:
nx.average_shortest_path_length(nx.Graph(sub_mat))

4.3942280748748574

- 表示在社群網路中兩個用戶之間的連接比較不緊密。

計算diameter（最長 shortest path 長度）

In [ ]:
nx.diameter(nx.Graph(sub_mat))

12

- 代表社群網路的整體規模比較大，不同群體之間的連接比較鬆散。
- 推測可能是此社群網路中存在大量用戶群體，不同群體之間的互動較少。

計算 clustering

In [ ]:
nx.average_clustering(nx.Graph(sub_mat))

0.006278427931450149

- clustering＝0，代表圖中不存在任何三角形。
- 可能代表社群網路中的用戶之間的聯繫較為鬆散，彼此之間的互動較少。


**結論**

根據社群網路圖，我們可以發現PTT上討論俄烏戰爭議題的主要群體有哪些，而哪些網友較能扮演此議題的關鍵角色、引起較大的討論度。  
  
另外，也可以發現在這個議題中，用戶之間的關係較為鬆散、聯繫不緊密等問題，較難形成穩定的社群網路，本組推測原因為：

1. 資料是從八卦版、政黑版爬下來的，這兩個版都是屬於PTT上流量較大、較熱門的版，因此文章更新的速度很快，對此議題關注用戶較難以隨時掌握資訊。
2. 並不是從專業的版（如美食版、棒球版等）探討特定的主題，因此留言的用戶也不太固定。
3. PTT是匿名的論壇，這也使得用戶之間的互動更加隨意，缺乏長期的信任和穩定的互動關係，不利於形成穩定的社群結構。
4. 在此議題上，缺乏能夠持續引導和凝聚討論的核心意見領袖，使得討論容易分散。
